In [1]:
# for auto-reloading extenrnal modules
# see http://stackoverflow.com/questions/1907993/autoreload-of-modules-in-ipython
%load_ext autoreload
%autoreload 2

from utils.show_mesh import *
from utils.symmetry_vect import *
from utils.curvature import *
from utils.visualization_tool import *

In [6]:
mesh = trimesh.load_mesh('meshes/jug.obj')

# For convenience, collect matrices of vertices (nv x 3) and triangles (nt x 3)
X = mesh.vertices; # each row is the position of a vertex
I,J,K = tri_indices(mesh.faces)
T = np.column_stack((I,J,K)) # rows are (i,j,k) indices of triangle vertices
nv = X.shape[0] # number of vertices
nt = T.shape[0] # number of triangles

textured_mesh(mesh)

In [295]:
curvatures = get_curvatures(mesh)

In [346]:
import random

n_samples = nv
n_subsamples = int(nv / 5)
mask = np.vectorize(lambda i : curvatures[i].valid)(range(nv))
valid_points = np.arange(nv)[mask == True]
sample = random.choices(valid_points, k=n_samples)
subsample = random.choices(valid_points, k=int(n_subsamples))

In [347]:
signatures = np.vectorize(lambda i : signature(mesh, curvatures, i))(np.arange(n_samples))
principle_curvatures = np.stack([curvatures[i].prin_curvatures for i in range(n_samples)])
visualize_point_2D(principle_curvatures)

In [348]:
symm = []
for i in range(int(n_subsample)):
    for j in range(n_samples):
        if subsample[i] != sample[j] and symmetry_test(mesh, curvatures, subsample[i], sample[j], threshold=1e-8):
            symm.append(get_symmetry_vect(mesh, curvatures, subsample[i], sample[j]))
symm = np.stack(symm)

In [351]:
symm = symm[:600]

In [352]:
from multiprocessing import Pool
import itertools

indices = list(itertools.product(list(range(symm.shape[0])), list(range(symm.shape[0]))))

pool = Pool(20)
def dist_array(i,j):
    return symmetry_dist(symm[i,:], symm[j,:])
results = pool.starmap(dist_array, indices)
'''
dissim = np.zeros((symm.shape[0], symm.shape[0]))
for i in range(symm.shape[0]):
    if i%20 == 0:
        print(i)
    for j in range(symm.shape[0]):
        dissim[i,j] = symmetry_dist(symm[i,:], symm[j,:])
'''
dissim = np.array(results).reshape(symm.shape[0],-1)

In [356]:
Lie_alg = np.stack([log_map(symm[i,:]) for i in range(symm.shape[0])])
visualize_point_3D(Lie_alg)
visualize_point_3D(Lie_alg, axis = [3,4,5])

In [370]:
dissim = dissim[~np.isnan(dissim)]
dissim = dissim.reshape(int(np.sqrt(dissim.shape[0])), -1)
visualize_dist_3D(dissim)

/home/dcy/anaconda3/lib/python3.7/site-packages/plotly/graph_objs/_deprecations.py:39: DeprecationWarning:

plotly.graph_objs.Data is deprecated.
Please replace it with a list or tuple of instances of the following types
  - plotly.graph_objs.Scatter
  - plotly.graph_objs.Bar
  - plotly.graph_objs.Area
  - plotly.graph_objs.Histogram
  - etc.




In [357]:
from sklearn.cluster import DBSCAN
clustering = DBSCAN(eps=0.7, min_samples=20, metric='precomputed').fit(dissim)
visualize_point_3D(Lie_alg[clustering.core_sample_indices_])

ValueError: Input contains NaN, infinity or a value too large for dtype('float64').